# Full Transfer Functions

In [1]:
%load_ext autoreload
import sys
sys.path.append("..")

In [23]:
%autoreload

import matplotlib
matplotlib.rc_file('matplotlibrc')
import matplotlib.pyplot as plt

%matplotlib inline

matplotlib.rcParams['figure.figsize'] = [10,10]


from astropy.io import fits

import numpy as np
import copy
import pickle

import darkhistory.physics as phys
import darkhistory.utilities as utils
import darkhistory.spec.spectools as spectools
import darkhistory.spec.transferfunction as tf
import darkhistory.spec.transferfunclist as tflist
from darkhistory.spec.spectrum import Spectrum
from darkhistory.spec.spectra import Spectra
import darkhistory.history.tla as tla

from scipy.interpolate import interp1d

from tqdm import tqdm_notebook as tqdm

from darkhistory.electrons.ics.ics_spectrum import ics_spec
from darkhistory.electrons.ics.ics_engloss_spectrum import engloss_spec
from darkhistory.electrons.ics.ics_cooling import get_ics_cooling_tf

from darkhistory.low_energy.lowE_deposition import compute_fs

# np.set_printoptions(threshold=np.nan)

In [3]:
mDM = 1e11
sigmav = 1e-24

def rate_func_swave(rs):
    return phys.inj_rate('swave', rs, mDM=mDM, sigmav=sigmav)/(2*mDM)

def test(rs, x1, x2, x3):
    return 0.3

test = tla.get_history(
                np.array([phys.TCMB(200), 2e-4, 0, 0]), 0.3, 0.3, 0.3, 
                rate_func_swave, np.array([200, 199.5, 199]), reion_switch=True
            )
print(test)

[[4.69730658e-02 2.00000000e-04 9.99998695e-13 9.99998695e-13]
 [4.67388268e-02 1.99892436e-04 9.99998695e-13 9.99998695e-13]
 [4.65058188e-02 1.99784748e-04 9.99998695e-13 9.99998695e-13]]


## Photon Transfer Functions

In [4]:
user = 'hongwan'

highengphot_tflist_arr = pickle.load(open("/Users/"+user+"/Dropbox (MIT)/Photon Deposition/tfunclist_photspec_60eV_complete_coarse.raw", "rb"))
lowengphot_tflist_arr  = pickle.load(open("/Users/"+user+"/Dropbox (MIT)/Photon Deposition/tfunclist_lowengphotspec_60eV_complete_coarse.raw", "rb"))
lowengelec_tflist_arr  = pickle.load(open("/Users/"+user+"/Dropbox (MIT)/Photon Deposition/tfunclist_lowengelecspec_60eV_complete_coarse.raw", "rb"))
CMB_engloss_arr = pickle.load(open("/Users/"+user+"/Dropbox (MIT)/Photon Deposition/CMB_engloss_60eV_complete_coarse.raw", "rb"))

In [5]:
highengphot_tflist_arr[0]._grid_vals.shape

(51, 325, 500)

In [6]:
photeng = highengphot_tflist_arr[0].eng
eleceng = lowengelec_tflist_arr[0].eng

#Split photeng into high and low energy. 
photeng_high = photeng[photeng > 60]
photeng_low  = photeng[photeng <= 60]

# Split eleceng into high and low energy. 
eleceng_high = eleceng[eleceng > 3000]
eleceng_low  = eleceng[eleceng <= 3000]


for highengphot_tflist in highengphot_tflist_arr:
    
#     highengphot_tflist.at_val('in_eng', photeng_high, bounds_error=False, fill_value=0)

    for tf in highengphot_tflist:
        # tf.rebin(photeng_high)
#         tf.rebin(photeng)
        
        # Pad with zeros so that it becomes photeng x photeng. 
        tf._grid_vals = np.pad(tf.grid_vals, ((photeng_low.size, 0), (0, 0)), 'constant')
        tf._N_underflow = np.pad(tf._N_underflow, (photeng_low.size, 0), 'constant')
        tf._eng_underflow = np.pad(tf._eng_underflow, (photeng_low.size, 0), 'constant')
        tf._in_eng = photeng
        tf._eng = photeng
        tf._rs = tf.rs[0]*np.ones_like(photeng)
    
    highengphot_tflist._eng = photeng
    highengphot_tflist._in_eng = photeng
    highengphot_tflist._grid_vals = np.atleast_3d(
        np.stack([tf.grid_vals for tf in highengphot_tflist._tflist])
    )
    
# lowengphot_tflist.in_eng set to photeng_high
for lowengphot_tflist in lowengphot_tflist_arr:
    
#     lowengphot_tflist.at_val('in_eng', photeng_high, bounds_error=False, fill_value=0)
    
    for tf in lowengphot_tflist:
#         tf.rebin(photeng)
        # Pad with zeros so that it becomes photeng x photeng. 
        tf._grid_vals = np.pad(tf.grid_vals, ((photeng_low.size,0), (0,0)), 'constant')
        # Photons in the low energy bins should be immediately deposited.
        tf._grid_vals[0:photeng_low.size, 0:photeng_low.size] = np.identity(photeng_low.size)
        tf._N_underflow = np.pad(tf._N_underflow, (photeng_low.size, 0), 'constant')
        tf._eng_underflow = np.pad(tf._eng_underflow, (photeng_low.size, 0), 'constant')
        tf._in_eng = photeng
        tf._eng = photeng
        tf._rs = tf.rs[0]*np.ones_like(photeng)
    
    lowengphot_tflist._eng = photeng
    lowengphot_tflist._in_eng = photeng
    lowengphot_tflist._grid_vals = np.atleast_3d(
        np.stack([tf.grid_vals for tf in lowengphot_tflist._tflist])
    )
    
# lowengelec_tflist.in_eng set to photeng_high 
for lowengelec_tflist in lowengelec_tflist_arr:
    
#     lowengelec_tflist.at_val('in_eng', photeng_high, bounds_error=False, fill_value=0)
    
    for tf in lowengelec_tflist:
#         tf.rebin(eleceng)
        # Pad with zeros so that it becomes photeng x eleceng. 
        tf._grid_vals = np.pad(tf.grid_vals, ((photeng_low.size,0), (0,0)), 'constant')
        tf._N_underflow = np.pad(tf._N_underflow, (photeng_low.size, 0), 'constant')
        tf._eng_underflow = np.pad(tf._eng_underflow, (photeng_low.size, 0), 'constant')
        tf._in_eng = photeng
        tf._eng = eleceng
        tf._rs = tf.rs[0]*np.ones_like(photeng)

    lowengelec_tflist._eng = eleceng
    lowengelec_tflist._in_eng = photeng
    lowengelec_tflist._grid_vals = np.atleast_3d(
        np.stack([tf.grid_vals for tf in lowengelec_tflist._tflist])
    )
    
    for engloss in CMB_engloss_arr:
        engloss = np.pad(engloss, ((0,0),(photeng_low.size, 0)), 'constant')


In [7]:
highengphot_tflist._grid_vals.shape

(51, 500, 500)

In [8]:
xes = 0.5 + 0.5*np.tanh([-5., -4.1, -3.2, -2.3, -1.4, -0.5, 0.4, 1.3, 2.2, 3.1, 4])


In [9]:
highengphot_tf_interp = tflist.TransferFuncInterp(xes, highengphot_tflist_arr)
lowengphot_tf_interp = tflist.TransferFuncInterp(xes, lowengphot_tflist_arr)
lowengelec_tf_interp = tflist.TransferFuncInterp(xes, lowengelec_tflist_arr)


phot_spec_init = spectools.rebin_N_arr(np.array([2]), 
                                      np.array([1e11]), 
                                      photeng)
phot_spec_init.switch_spec_type()


In [45]:
phot_spec_init.rs = 203
end_rs   = 50
mDM = 1e8
sigmav = 1e-24

def rate_func_swave(rs):
    return phys.inj_rate('swave', rs, mDM=mDM, sigmav=sigmav)/(2*mDM)

def evolve(
    in_spec_elec, in_spec_phot, 
    rate_func, xe_init, T_m_init,
    highengphot_tf_interp, lowengphot_tf_interp, 
    lowengelec_tf_interp, 
    end_rs, coarsen_factor=1, save_steps=True
):
    """
    Main function that computes the temperature and ionization history. 
    
    Parameters
    ----------
    in_spec_elec : Spectrum
        Spectrum per annihilation/decay into electrons. 
    in_spec_phot : Spectrum
        Spectrum per annihilation/decay into photons.
    rate_func : function
        Function describing the rate of annihilation/decay, dN/(dV dt)
    xe_init : float
        xe at the initial redshift. 
    T_m_init : float
        Matter temperature at the initial redshift. 
    highengphot_tf_interp : TransferFuncInterp
        Interpolation table for high energy photons. 
    lowengphot_tf_interp : TransferFuncInterp
        Interpolation table for low energy photons. 
    lowengelec_tf_interp : TransferFuncInterp
        Interpolation table for low energy electrons. 
    end_rs : float
        Final redshift to evolve to. 
    coarsen_factor : int
        Coarsening to apply to the transfer function matrix. 
    save_steps : bool
        Whether to save all intermediate spectra. 
    """
    
    # Initialize the next spectrum as None.
    next_highengphot_spec = None
    next_lowengphot_spec  = None
    next_lowengelec_spec  = None
    
    if (
        highengphot_tf_interp.dlnz    != lowengphot_tf_interp.dlnz
        or highengphot_tf_interp.dlnz != lowengelec_tf_interp.dlnz
        or lowengphot_tf_interp.dlnz  != lowengelec_tf_interp.dlnz
    ):
        raise TypeError('TransferFuncInterp objects must all have the same dlnz.')
    
    if in_spec_elec.rs != in_spec_phot.rs:
        raise TypeError('Input spectra must have the same rs.')
    
    # redshift/timestep related quantities. 
    dlnz = highengphot_tf_interp.dlnz
    prev_rs = None
    rs = in_spec_phot.rs
    dt = dlnz/phys.hubble(rs)
    
    # The initial input dN/dE per annihilation to per baryon per dlnz, 
    # based on the specified rate. 
    # dN/(dN_B d lnz dE) = dN/dE * (dN_ann/(dV dt)) * dV/dN_B * dt/dlogz
    
    # ICS for in_spec_elec goes here.
    
    init_inj_spec = (
        in_spec_phot * rate_func(rs) * dlnz
        / phys.hubble(rs) / (phys.nB * rs**3)
    )
    
    
    # Initialize the Spectra object that will contain all the 
    # output spectra during the evolution.
    out_highengphot_specs = Spectra([init_inj_spec], spec_type=init_inj_spec.spec_type)
    out_lowengphot_specs  = Spectra([], spec_type=init_inj_spec.spec_type)
    out_lowengelec_specs  = Spectra([], spec_type=init_inj_spec.spec_type)
    
    # Initialize the xe and T array that will store the solutions.
    xe_arr  = np.array([xe_init])
    T_m_arr = np.array([T_m_init])
    
    # Define these methods for speed.
    append_highengphot_spec = out_highengphot_specs.append
    append_lowengphot_spec  = out_lowengphot_specs.append
    append_lowengelec_spec  = out_lowengelec_specs.append
    
    # Loop while we are still at a redshift above end_rs.
    while rs > end_rs:
        
        print(rs)
        
        # If prev_rs exists, calculate xe and T_m. 
        if prev_rs is not None:
            print('here at least?')
            
             # f_continuum, f_lyman, f_ionH, f_ionHe, f_heat
            f_raw = compute_fs(
                next_lowengelec_spec, next_lowengphot_spec,
                np.array([xe_arr[-1], 0, 0]), rate_func(rs), dt
            )
            
            
            print(f_raw)
            
            init_cond = np.array([T_m_arr[-1], xe_arr[-1], 0, 0])
            print(init_cond)
            
            new_vals = tla.get_history(
                init_cond, f_raw[2], f_raw[1], f_raw[4], 
                rate_func_swave, np.array([prev_rs, rs])
            )
#             new_vals = tla.get_history(
#                 init_cond, 0.33, 0.33, 0.33, 
#                 rate_func_swave, np.array([prev_rs, rs])
#             )
    
            print(new_vals)
            
            T_m_arr = np.append(T_m_arr, new_vals[-1,0])
            xe_arr  = np.append(xe_arr,  new_vals[-1,1])
            
        print(T_m_arr)
        print(xe_arr)
        
        highengphot_tf = highengphot_tf_interp.get_tf(rs, xe_arr[-1])
        lowengphot_tf  = lowengphot_tf_interp.get_tf(rs, xe_arr[-1])
        lowengelec_tf  = lowengelec_tf_interp.get_tf(rs, xe_arr[-1])
        
#         if coarsen_factor > 1:
#             prop_tf = np.zeros_like(highengphot_tf._grid_vals)
#             for i in np.arange(coarsen_factor):
#                 prop_tf += matrix_power(highengphot_tf._grid_vals, i)
#             lowengphot_tf._grid_vals = np.matmul(prop_tf, lowengphot_tf._grid_vals)
#             lowengelec_tf._grid_vals = np.matmul(prof_tf, lowengelec_tf._grid_vals)
#             highengphot_tf._grid_vals = matrix_power(
#                 highengphot_tf._grid_vals, coarsen_factor
#             )
            
        next_highengphot_spec = highengphot_tf.sum_specs(out_highengphot_specs[-1])
        next_lowengphot_spec  = lowengphot_tf.sum_specs(out_highengphot_specs[-1])
        next_lowengelec_spec  = lowengelec_tf.sum_specs(out_highengphot_specs[-1])
        
        # Re-define existing variables.
        prev_rs = rs
        rs = np.exp(np.log(rs) - 0.002)
        
        dt = dlnz/phys.hubble(rs)
        next_highengphot_spec.rs = rs
        next_lowengphot_spec.rs  = rs
        next_lowengelec_spec.rs  = rs
        
        # Add the next injection spectrum to next_highengphot_spec
        next_inj_spec = (
            in_spec_phot * rate_func(rs) 
            / phys.hubble(rs) / (phys.nB * rs**3)
        )
        next_highengphot_spec += next_inj_spec
        
        append_highengphot_spec(next_highengphot_spec)
        append_lowengphot_spec(next_lowengphot_spec)
        append_lowengelec_spec(next_lowengelec_spec)
        
        print('here?')
        
    return (
        xe_arr, T_m_arr, 
        out_highengphot_specs, out_lowengphot_specs, out_lowengelec_specs
    )
        
        
            
        
            
    


In [46]:
%%prun
a = evolve(
    phot_spec_init*0, phot_spec_init, 
    rate_func_swave, 2e-4, phys.TCMB(phot_spec_init.rs),
    highengphot_tf_interp, lowengphot_tf_interp, 
    lowengelec_tf_interp, 
    end_rs, coarsen_factor=1, save_steps=True
)

203
[0.04767766]
[0.0002]
here?
202.59440572946863
here at least?
[9.49269867e+02 1.40740739e+02 8.57441583e+02 7.27798642e-12
 4.49439202e+03]
[0.04767766 0.0002     0.         0.        ]
[[4.76776618e-02 2.00000000e-04 9.99998695e-13 9.99998695e-13]
 [4.74929363e-02 2.00036202e-04 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294]
[0.0002     0.00020004]
here?
202.18962183683033
here at least?
[4.77827482e+05 7.07644485e+04 4.31101651e+05 3.66190099e-09
 2.26103761e+06]
[0.04749294 0.00020004 0.         0.        ]
[[4.74929363e-02 2.00036202e-04 9.99998695e-13 9.99998695e-13]
 [5.00004568e-02 2.61695795e-04 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046]
[0.0002     0.00020004 0.0002617 ]
here?
201.78564670294895
here at least?
[1.57187747e+06 1.95460845e+05 1.16724299e+06 1.18761344e-08
 6.28331421e+06]
[0.05000046 0.0002617  0.         0.        ]
[[5.00004568e-02 2.61695795e-04 9.99998695e-13 9.99998695e-13]
 [5.72398287e-02 4.28220426e-04 9.99998695e-13 

../darkhistory/spec/spectrum.py:748: RuntimeWarning: The new abscissa lies below the old one: only bins that lie within the new abscissa will be rebinned, bins above the abscissa will be discarded.
  warnings.warn("The new abscissa lies below the old one: only bins that lie within the new abscissa will be rebinned, bins above the abscissa will be discarded.", RuntimeWarning)


here?
200.57855771097212
here at least?
[4.10542209e+06 3.91083022e+05 2.30626034e+06 1.66176398e-07
 1.39915747e+07]
[0.08161703 0.00095824 0.         0.        ]
[[8.16170344e-02 9.58237349e-04 9.99998695e-13 9.99998695e-13]
 [9.67234181e-02 1.28308510e-03 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342]
[0.0002     0.00020004 0.0002617  0.00042822 0.00066795 0.00095824
 0.00128309]
here?
200.17780148536124
here at least?
[4.63205388e+06 4.21721653e+05 2.48489163e+06 4.42995011e-07
 1.54676882e+07]
[0.09672342 0.00128309 0.         0.        ]
[[9.67234181e-02 1.28308510e-03 9.99998695e-13 9.99998695e-13]
 [1.12618373e-01 1.63131436e-03 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342 0.11261837]
[0.0002     0.00020004 0.0002617  0.00042822 0.00066795 0.00095824
 0.00128309 0.00163131]
here?
199.7778459712232
here at least?
[5.02881928e+06 4.42903556e+05 2.6099

here?
193.48615877673444
here at least?
[6.23438734e+06 5.02611197e+05 2.98021341e+06 2.55603717e+01
 2.06005354e+07]
[0.20797792 0.00765887 0.         0.        ]
[[2.07977917e-01 7.65887035e-03 9.99998695e-13 9.99998695e-13]
 [2.04053777e-01 8.01501221e-03 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342 0.11261837 0.12859569 0.14407304 0.15858864 0.17179342
 0.18344124 0.19337824 0.20153163 0.2078981  0.21253204 0.21553377
 0.21703816 0.21720392 0.21620383 0.21421626 0.21141787 0.20797792
 0.20405378]
[0.0002     0.00020004 0.0002617  0.00042822 0.00066795 0.00095824
 0.00128309 0.00163131 0.00199508 0.00236888 0.00274891 0.00313256
 0.00351805 0.00390409 0.00428977 0.00467438 0.00505736 0.00543826
 0.00581667 0.00619221 0.00656453 0.0069333  0.00729819 0.00765887
 0.00801501]
here?
193.09957317364598
here at least?
[6.25680782e+06 5.03912063e+05 2.98747319e+06 6.90027050e+01
 2.06631302e+07]
[0.20405378 0.00801501 0.    

[0.16483661 0.01096751 0.         0.        ]
[[1.64836610e-01 1.09675071e-02 9.99998695e-13 9.99998695e-13]
 [1.61183081e-01 1.12629995e-02 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342 0.11261837 0.12859569 0.14407304 0.15858864 0.17179342
 0.18344124 0.19337824 0.20153163 0.2078981  0.21253204 0.21553377
 0.21703816 0.21720392 0.21620383 0.21421626 0.21141787 0.20797792
 0.20405378 0.19978792 0.19530602 0.19071603 0.18610803 0.18155453
 0.17711055 0.17281574 0.1687179  0.16483661 0.16118308]
[0.0002     0.00020004 0.0002617  0.00042822 0.00066795 0.00095824
 0.00128309 0.00163131 0.00199508 0.00236888 0.00274891 0.00313256
 0.00351805 0.00390409 0.00428977 0.00467438 0.00505736 0.00543826
 0.00581667 0.00619221 0.00656453 0.0069333  0.00729819 0.00765887
 0.00801501 0.0083663  0.00871242 0.00905307 0.00938797 0.00971685
 0.01003945 0.01035558 0.01066499 0.01096751 0.011263  ]
here?
189.2759454409089
here at least?
[6.4

...

[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342 0.11261837 0.12859569 0.14407304 0.15858864 0.17179342
 0.18344124 0.19337824 0.20153163 0.2078981  0.21253204 0.21553377
 0.21703816 0.21720392 0.21620383 0.21421626 0.21141787 0.20797792
 0.20405378 0.19978792 0.19530602 0.19071603 0.18610803 0.18155453
 0.17711055 0.17281574 0.1687179  0.16483661 0.16118308 0.15776157
 0.15457083 0.15160547 0.14885703 0.14631496 0.14396738 0.14180173
 0.13980521 0.13796518 0.1362694  0.13471028 0.1332835  0.13197724
 0.13077977 0.12968068 0.12867063 0.12774132 0.12688533 0.12609606
 0.12536765 0.12469488 0.12407309 0.12349814 0.12296631 0.12247429
 0.12201908 0.12159801 0.12120865 0.1208488  0.12051647 0.12020984
 0.11992725 0.11966717 0.11942823 0.11920912 0.11900866 0.11882576
 0.1186594  0.11850865 0.11837262 0.1182505  0.11814153 0.118045
 0.11796025 0.11788665 0.11782363 0.11777064 0.11772716 0.11769272
 0.11766685 0.11764915 0.1176392  0.11763662 0.11764106 0.117652

here?
51.17268937270112
here at least?
[1.30675795e+08 4.07752848e+06 1.83861803e+07 1.68249341e+03
 1.38995703e+08]
[0.41603585 0.06058498 0.         0.        ]
[[4.16035847e-01 6.05849821e-02 9.99998695e-13 9.99998695e-13]
 [4.17086299e-01 6.07133310e-02 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342 0.11261837 0.12859569 0.14407304 0.15858864 0.17179342
 0.18344124 0.19337824 0.20153163 0.2078981  0.21253204 0.21553377
 0.21703816 0.21720392 0.21620383 0.21421626 0.21141787 0.20797792
 0.20405378 0.19978792 0.19530602 0.19071603 0.18610803 0.18155453
 0.17711055 0.17281574 0.1687179  0.16483661 0.16118308 0.15776157
 0.15457083 0.15160547 0.14885703 0.14631496 0.14396738 0.14180173
 0.13980521 0.13796518 0.1362694  0.13471028 0.1332835  0.13197724
 0.13077977 0.12968068 0.12867063 0.12774132 0.12688533 0.12609606
 0.12536765 0.12469488 0.12407309 0.12349814 0.12296631 0.12247429
 0.12201908 0.12159801 0.12120865 0.1208

here?
50.76494102576284
here at least?
[1.33137591e+08 4.13767849e+06 1.86178924e+07 1.71630840e+03
 1.40661387e+08]
[0.42023352 0.06109962 0.         0.        ]
[[4.20233520e-01 6.10996178e-02 9.99998695e-13 9.99998695e-13]
 [4.21281070e-01 6.12287779e-02 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342 0.11261837 0.12859569 0.14407304 0.15858864 0.17179342
 0.18344124 0.19337824 0.20153163 0.2078981  0.21253204 0.21553377
 0.21703816 0.21720392 0.21620383 0.21421626 0.21141787 0.20797792
 0.20405378 0.19978792 0.19530602 0.19071603 0.18610803 0.18155453
 0.17711055 0.17281574 0.1687179  0.16483661 0.16118308 0.15776157
 0.15457083 0.15160547 0.14885703 0.14631496 0.14396738 0.14180173
 0.13980521 0.13796518 0.1362694  0.13471028 0.1332835  0.13197724
 0.13077977 0.12968068 0.12867063 0.12774132 0.12688533 0.12609606
 0.12536765 0.12469488 0.12407309 0.12349814 0.12296631 0.12247429
 0.12201908 0.12159801 0.12120865 0.1208

here?
50.461263323746905
here at least?
[1.34983849e+08 4.18277528e+06 1.87914116e+07 1.74179691e+03
 1.41907690e+08]
[0.42337366 0.06148767 0.         0.        ]
[[4.23373660e-01 6.14876671e-02 9.99998695e-13 9.99998695e-13]
 [4.24418638e-01 6.16173872e-02 9.99998695e-13 9.99998695e-13]]
[0.04767766 0.04749294 0.05000046 0.05723983 0.06813423 0.08161703
 0.09672342 0.11261837 0.12859569 0.14407304 0.15858864 0.17179342
 0.18344124 0.19337824 0.20153163 0.2078981  0.21253204 0.21553377
 0.21703816 0.21720392 0.21620383 0.21421626 0.21141787 0.20797792
 0.20405378 0.19978792 0.19530602 0.19071603 0.18610803 0.18155453
 0.17711055 0.17281574 0.1687179  0.16483661 0.16118308 0.15776157
 0.15457083 0.15160547 0.14885703 0.14631496 0.14396738 0.14180173
 0.13980521 0.13796518 0.1362694  0.13471028 0.1332835  0.13197724
 0.13077977 0.12968068 0.12867063 0.12774132 0.12688533 0.12609606
 0.12536765 0.12469488 0.12407309 0.12349814 0.12296631 0.12247429
 0.12201908 0.12159801 0.12120865 0.120

[0.0002     0.00020004 0.0002617  0.00042822 0.00066795 0.00095824
 0.00128309 0.00163131 0.00199508 0.00236888 0.00274891 0.00313256
 0.00351805 0.00390409 0.00428977 0.00467438 0.00505736 0.00543826
 0.00581667 0.00619221 0.00656453 0.0069333  0.00729819 0.00765887
 0.00801501 0.0083663  0.00871242 0.00905307 0.00938797 0.00971685
 0.01003945 0.01035558 0.01066499 0.01096751 0.011263   0.01155135
 0.01183247 0.01210632 0.01237286 0.0126321  0.01288405 0.01312877
 0.01336632 0.01359678 0.01382025 0.0140369  0.01424696 0.01445064
 0.0146481  0.01483947 0.01502493 0.01520461 0.01537868 0.0155473
 0.01571062 0.0158688  0.016022   0.01617037 0.01631407 0.01645325
 0.01658806 0.01671865 0.01684517 0.01696775 0.01708655 0.01720169
 0.01731331 0.01742154 0.01752651 0.01762834 0.01772715 0.01782306
 0.01791619 0.01800663 0.01809451 0.01817992 0.01826296 0.01834373
 0.01842232 0.01849882 0.01857331 0.01864588 0.01871662 0.01878559
 0.01885287 0.01891853 0.01898264 0.01904526 0.01910647 0.01916

In [ ]:
b = 2.
isinstance(b, float)

In [ ]:
compute_fs( 0*a, a,
    np.array([2e-4, 0, 0]), rate_func_swave(rs), dt
            )

In [ ]:
a